# Notes

DHC key metrics

- thermal load density
- load factor (average / peak load)
- diversity factor (central equipment design load / sum of peak load)

## *ASHRAE HVAC Application CHAPTER 34 GEOTHERMAL ENERGY*

The following classification by temperature is used in the geothermal industry:

- High temperature t > 150°C
- Intermediate temperature 90°C < t < 150°C
- Low temperature t < 90°C

> Electric generation is generally not economical for resources
with temperatures below about 150°C, which is the reason for the
division between high- and intermediate-temperature. However,
binary (organic Rankine cycle) power plants, with the proper set of
circumstances, have demonstrated that it is possible to generate
electricity economically above 110°C. In 1988, there were 86
binary plants worldwide, generating a total of 126.3 MW (Di Pippo
1988).

Hybrid systems are a variation of ground-coupled systems in
which a smaller ground loop is used, augmented in cooling mode by
a fluid cooler or a cooling tower. This approach can have merit in
large cooling-dominated applications. The ground loop is sized to
meet the heating requirements. The downsized loop is used in con-
junction with the fluid cooler or cooling tower with an isolation heat
exchanger to meet the heat rejection load. Using the cooler reduces
the capital cost of the ground loop in such applications, but some-
what increases maintenance requirements. For heavily heating-
dominant applications, a downsized loop also can be augmented with
an auxiliary heat source such as electric resistance, solar collectors,
or fossil fuel.

## *Analysis of the impact of storage conditions on the thermal recovery efficiency of low-temperature ATES systems*

> The energy demand profile of ATES systems varies due to variations
in weather conditions and building use which is of importance for the
actual value of the thermal efficiency. For 12 varying scenarios the
efficiencies are determined for both a weather dependent and the reg-
ular energy demand profile, showing that the efficiencies of the corre-
sponding conditions differ. However, they show the same relation ac-
cording to the changes in conditions; the Pearson correlation coefficient
of the two simulation result collections is 0,97. Based on this evaluation
all simulations are done with one basic energy demand profile

# Constants & conversion factors

In [1]:
# Select node for analysis
node = 'Biosciences'

In [2]:
# Constants
# Careful: Absorption chiller efficiency is homogeneous to a COP (heat flow rate/power) whereas electric chiller efficiency is in kW/ton so 1/EER!!!
file_path = '/home/agautier/Downloads/2019-05-31 Building energy and loads.xlsx'
sheet_name = 'Inputs'
df = pd.read_excel(file_path, sheet_name, skiprows=11, nrows=11)
df = df[[x for x in df.columns if 'Unnamed' not in x]]
df.rename(lambda x: re.sub(' ', '', x), axis='columns', inplace=True)
cst = df.copy()
cst = pd.concat([
    cst,
    pd.DataFrame(dict(
        Parameter=['J/Btu', 'kW/ton', 'kW/(kBtu/h)', 'J/kWh', 'm2/sqft'],
        Value=[1055.06, 3.51685, 1000 / 3600 * 1055.06 / 1000, 3.6e+6, 0.092903]))
])
cst.set_index('Parameter', inplace=True)
cst

/home/agautier/miniconda3/lib/python3.8/site-packages/openpyxl/worksheet/_reader.py:312: UserWarning:

Conditional Formatting extension is not supported and will be removed



Value       Unit  \
Parameter                                                       
Existing building-level steam loss    1.500000e-01          %   
Enthalpy                              9.700000e+02     Btu/lb   
Btu/kBtu                              1.000000e+03   Btu/kBtu   
Gas efficiency                        8.000000e-01          %   
Btu per W                             3.412000e+00      Btu/W   
Btu per therm                         1.000000e+05  Btu/therm   
Absorption chiller efficiency         4.000000e-01        COP   
Existing electric chiller efficiency  1.250000e+00     kW/ton   
New electric chiller efficiency       5.000000e-01     kW/ton   
Building heating system efficiency    9.500000e-01          %   
Btuh per ton                          1.200000e+04   Btuh/ton   
J/Btu                                 1.055060e+03        NaN   
kW/ton                                3.516850e+00        NaN   
kW/(kBtu/h)                           2.930722e-01        NaN   
J/kWh                                 3.600000e+06        NaN   
m2/sqft                               9.290300e-02        NaN   

                                                                                 Source  
Parameter                                                                                
Existing building-level steam loss    Assumption to convert from steam usage to heat...  
Enthalpy                                                                            NaN  
Btu/kBtu                                                                       Constant  
Gas efficiency                                                               Assumption  
Btu per W                                                                      Constant  
Btu per therm                                                                  Constant  
Absorption chiller efficiency         Assumption based on average chiller age and di...  
Existing electric chiller efficiency  Assumption based on average chiller age and di...  
New electric chiller efficiency       Assumption based on average chiller age and di...  
Building heating system efficiency    Assumption to convert from steam usage to heat...  
Btuh per ton                                                                   Constant  
J/Btu                                                                               NaN  
kW/ton                                                                              NaN  
kW/(kBtu/h)                                                                         NaN  
J/kWh                                                                               NaN  
m2/sqft                                                                             NaN

# Loads and energy use

## Peak loads

In [233]:
file_path = '/home/agautier/Downloads/2019-05-31 Building energy and loads.xlsx'
sheet_name = 'Peak Load Calc'
df = pd.read_excel(file_path, sheet_name, skiprows=12)
missing_names = ['CAAN','Building Name','Building Type','Year Constructed',	'Year Demolished',	
                 'Building Area (sqft)', 'Node', 'Cluster']
df.columns.values[1:9] = missing_names
df.columns.values[9] = 'Cooling Type'
df.columns.values[11] = 'Peak Steam Intensity (Btuh/sqft)'
df = df[[x for x in df.columns if 'Unnamed' not in x]]
df.rename(lambda x: re.sub(' ', '', x), axis='columns', inplace=True)
df = df[~df.BuildingType.isna()]
loa = df.copy()
# SI conversion (kW)
loa['PeakHeating'] = loa['PeakHeating'] * cst.at['kW/(kBtu/h)', 'Value']
loa['PeakCooling'] = loa['TotalChillerCapacity'] * cst.at['kW/ton', 'Value']
loa.tail()

/home/agautier/miniconda3/lib/python3.8/site-packages/openpyxl/worksheet/_reader.py:312: UserWarning:

Conditional Formatting extension is not supported and will be removed

/home/agautier/miniconda3/lib/python3.8/site-packages/openpyxl/worksheet/_reader.py:312: UserWarning:

Data Validation extension is not supported and will be removed



CAAN              BuildingName BuildingType  YearConstructed  \
114  1800  Lawrence Hall of Science    Classroom           1968.0   
115  1286               Tang Center        Admin           1993.0   
116  1033                 Chou Hall    Classroom           2018.0   
117  1787              Upper Hearst    Residence           2021.0   
118  1520        Bakar Bioenginuity   Bioscience           1970.0   

     YearDemolished  BuildingArea(sqft) Node Cluster       CoolingType  \
114             NaN            128540.0  NaN     NaN  Packaged VAV, DX   
115             NaN             75228.0  NaN     NaN  Packaged VAV, DX   
116             NaN             80000.0  NaN     NaN  Packaged VAV, DX   
117             NaN             54000.0  NaN     NaN  Packaged VAV, DX   
118             NaN            102794.0  NaN     NaN  Packaged VAV, DX   

     PeakSteamIntensity(Btuh/sqft)  ...  Process.3  SpaceHeating.1  DHW.4  \
114                          10.10  ...        NaN             NaN    NaN   
115                          10.10  ...        NaN             NaN    NaN   
116                          10.10  ...        NaN             NaN    NaN   
117                          14.14  ...        NaN             NaN    NaN   
118                          41.44  ...        NaN             NaN    NaN   

     Absorption.4  Process.4  SpaceHeating.2  DHW.5  Absorption.5  Process.5  \
114           NaN        NaN             NaN    NaN           NaN        NaN   
115           NaN        NaN             NaN    NaN           NaN        NaN   
116           NaN        NaN             NaN    NaN           NaN        NaN   
117           NaN        NaN             NaN    NaN           NaN        NaN   
118           NaN        NaN             NaN    NaN           NaN        NaN   

    PeakCooling  
114  452.055899  
115  264.565592  
116  281.348000  
117  132.936930  
118  903.777697  

[5 rows x 45 columns]

## Heating and cooling energy

Based on electricity and steam EU.

> Need to update cooling energy as currently design chiller COP is used to convert from electricity.

In [234]:
file_path = '/home/agautier/Downloads/2019-05-31 Building energy and loads.xlsx'
sheet_name = 'Annual Energy Calc'
df = pd.read_excel(file_path, sheet_name, skiprows=12)
missing_names = ['CAAN','Building Name','Building Type','Year Constructed',	'Year Demolished',	
                 'Building Area (sqft)', 'Node', 'Cluster']
df.columns.values[1:9] = missing_names
df.columns.values[10] = 'Electricity Use (kWh/y)'
df.columns.values[16] = 'Steam Use (kBtu/y)'
df = df[[x for x in df.columns if 'Unnamed' not in x]]
df.rename(lambda x: re.sub(' ', '', x), axis='columns', inplace=True)
df = df[~df.BuildingType.isna()]
eus = df.copy()

# Add distributed energy in kWh/y
eus['COP'] = 1 / (eus.apply(lambda x: loa.set_index('BuildingName').at[x.BuildingName, 'Efficiency(kW/ton)'], axis=1) / cst.at['kW/ton', 'Value'])
## Assumptions: Cooling = Cooling&HeatRejection and COP (kW/kW) = seasonal COP (kWh/kWh)
eus['CoolingElec'] = eus['ElectricityUse(kWh/y)'] * eus['Cooling&HeatRejection'] * eus['COP']
eus['SteamEnergy'] = eus['SteamUse(kBtu/y)'] * (1 - cst.at['Existing building-level steam loss', 'Value']) * 1000 *\
                     cst.loc['J/Btu'].Value / cst.at['J/kWh', 'Value']
eus['SpaceHeating'] = eus['SteamEnergy'] * eus['SpaceHeating']
eus['DHW'] = eus['SteamEnergy'] * eus['DHW']
eus['Process'] = eus['SteamEnergy'] * eus['Process']
# Careful: Absorption chiller efficiency is homogeneous to a COP (heat output/heat input) 
eus['CoolingAbsorption'] = eus['SteamEnergy'] * eus['Absorption'] * cst.at['Absorption chiller efficiency', 'Value']
eus['Cooling'] = eus['CoolingElec'] + eus['CoolingAbsorption'] 

eus.tail()

/home/agautier/miniconda3/lib/python3.8/site-packages/openpyxl/worksheet/_reader.py:312: UserWarning:

Conditional Formatting extension is not supported and will be removed



CAAN                                BuildingName BuildingType  \
96   1292 (N)                              Lewis Hall (N)    Chemistry   
97      CAAN?                         Lewis Hall Addition    Chemistry   
98       1785                                Oxford Tract    Residence   
99       1601                                Peoples Park    Residence   
100  1774 (N)  Tolman Hall (N) (Climate Science Building)   Bioscience   

     YearConstructed  YearDemolished  BuildingArea(sqft)  \
96            2040.0             NaN             87500.0   
97            2028.0             NaN             90000.0   
98            2025.0             NaN           1050000.0   
99            2023.0             NaN            432000.0   
100           2025.0             NaN            292500.0   

                                   Node            Cluster  \
96   Engineering, Physics and Chemistry  Engineering Lewis   
97   Engineering, Physics and Chemistry  Engineering Lewis   
98                          Biosciences       Oxford Tract   
99                 Lower Sproul offices       Peoples Park   
100                         Biosciences  Biosciences North   

     ElectricityUse(kWh/y)  Cooling&HeatRejection  ...  PlugsandMisc..2  \
96               4179700.0                   0.25  ...              NaN   
97               4299120.0                   0.25  ...              NaN   
98              11106060.0                   0.00  ...              NaN   
99               4569350.4                   0.00  ...              NaN   
100             13972140.0                   0.25  ...              NaN   

     SpaceHeating.2  DHW.2 Absorption.2  Process.2       COP   CoolingElec  \
96              NaN    NaN          NaN        NaN  2.842787  2.970499e+06   
97              NaN    NaN          NaN        NaN  2.842787  3.055371e+06   
98              NaN    NaN          NaN        NaN  6.011709  0.000000e+00   
99              NaN    NaN          NaN        NaN  6.011709  0.000000e+00   
100             NaN    NaN          NaN        NaN  6.011709  2.099911e+07   

      SteamEnergy  CoolingAbsorption       Cooling  
96   1.829879e+06                0.0  2.970499e+06  
97   1.882161e+06                0.0  3.055371e+06  
98   3.609624e+06                0.0  0.000000e+00  
99   1.485102e+06                0.0  0.000000e+00  
100  6.117024e+06                0.0  2.099911e+07  

[5 rows x 41 columns]

In [235]:
# Load factors - Node
LF_cooling = eus.set_index('Node').loc[node, 'Cooling'].sum() / 8760 / loa.set_index('Node').loc[node, 'PeakCooling'].sum()
LF_heating = (eus.set_index('Node').loc[node, 'SpaceHeating'] + eus.set_index('Node').loc[node, 'DHW']).sum() / 8760 /\
             loa.set_index('Node').loc[node, 'PeakHeating'].sum()
LF_cooling, LF_heating

(0.38916928920594046, 0.6038473822478909)

In [236]:
load_diversity = dict(
    heating_node=0.85,
    heating_campus=0.80,
    cooling_node=0.95,
    cooling_campus=0.90,
)

In [237]:
# Peak loads - Campus
loa['PeakHeating'].sum() * load_diversity['heating_campus'], loa['PeakCooling'].sum() * load_diversity['cooling_campus']  # kw

(67303.10263876154, 89011.676633256)

In [238]:
# Capacity weighted chiller efficiency COP (-)
# This is without heat recovery that requires higher condenser temperature so lower COP!
## Whole campus
COP_campus = 1 / (
        (loa['Efficiency(kW/ton)'] * loa['TotalChillerCapacity']).sum() /\
        loa['TotalChillerCapacity'].sum() / cst.at['kW/ton', 'Value'])
## Node
COP_node = 1 / (
(loa.set_index('Node').loc[node, 'Efficiency(kW/ton)'] *\
 loa.set_index('Node').loc[node, 'TotalChillerCapacity']).sum() /\
    loa.set_index('Node').loc[node, 'TotalChillerCapacity'].sum() / cst.at['kW/ton', 'Value'])
## Heat recovery COP from `Global Inputs` in `2020-04-20 UCB utilities calculation_accelerated phasing`
COP_HR = 1 / (1 / cst.at['kW/ton', 'Value'])
print(COP_campus, COP_node, COP_HR)

4.3497463340703 4.762747927832286 3.51685


## Hourly load profile

In [181]:
from scipy.optimize import minimize_scalar

In [245]:
peak_cooling = loa.set_index('Node').loc[node, 'PeakCooling'].sum() * load_diversity['cooling_node']  # kW
peak_heating = loa.set_index('Node').loc[node, 'PeakHeating'].sum() * load_diversity['heating_node']  # kW

From `2020-09-23 UCB load data to DOE`

> These hourly heating and cooling profiles were derived for the 2019 UC Berkeley Campus Energy Plan to estimate heat recovery potential and thermal storage tank size. These profiles were created using Arup's in-house District Energy Feasibility (DEF) tool. The DEF tool takes in location, building area by use type (office, residential, etc.), and building age, estimates load for each building type using PNNL’s commercial building reference models, and scales to match the input on a sqft basis. ***The resulting campus profiles were scaled linearly so that the peaks matched actual peak loads (derived from measured steam and electricity usage and installed chiller capacity).***

This scaling method applied to the node yields annual cooling (heating) energy 3 (2) times lower than the one from `Annual Energy Calc`.

In [246]:
file_path = '/home/agautier/Downloads/2020-09-23 UCB load data to DOE.xlsx'
sheet_name = 'Hourly load profiles'
df = pd.read_excel(file_path, sheet_name, skiprows=11)
df.rename(lambda x: re.sub(' ', '', x), axis='columns', inplace=True)
df.Date = pd.to_datetime(df.Date)
df.set_index('Date', inplace=True)
# SI conversion: kBtu/h to kW
df.loc[:, ['Cooling', 'Heating']] *= cst.loc['kW/(kBtu/h)'].Value
# df = df[['Date', 'Cooling', 'Heating']].melt(id_vars='Date')
lot = df[['Cooling', 'Heating']].copy()
# Add month and hour of day and max heat flow rate from condenser heat recovery
lot['month'] = lot.index.month
lot['hour'] = lot.index.hour

lot['Cooling_raw'] = lot.Cooling.copy()
lot['Heating_raw'] = lot.Heating.copy()

# Scale for peak load     
scp_cooling = peak_cooling / lot.Cooling.max()
scp_heating = peak_heating / lot.Heating.max()
lot.Cooling = lot.Cooling * scp_cooling
lot.Heating = lot.Heating * scp_heating

# Scale for integral load under the constraint of unchanged range
# Including DHW in heating, excluding process = same assumption as 'Peak Heating' in 'Peak Load Calc'
eus_cooling = eus.set_index('Node').loc[node, 'Cooling'].sum()
eus_heating = (eus.set_index('Node').loc[node, 'SpaceHeating'] + eus.set_index('Node').loc[node, 'DHW']).sum()


def scale(q, k, qmin, qmax, qmean):
    if q < qmean:
        y = (k * qmean  - qmin) / (qmean - qmin) * (q - qmin) + qmin
        return max(qmin, y)
    else:
        y = (k * qmean  - qmax) / (qmean - qmax) * (q - qmax) + qmax
        return min(qmax, y) 

    
for typ in ['Cooling', 'Heating']:
    if typ == 'Heating':
        eus_actual = eus_heating
    else:
        eus_actual = eus_cooling
        
    def obj(k):
        tmp = lot[typ].resample("60min").mean()
        return (tmp.apply(scale, args=(k, tmp.min(), tmp.max(), tmp.mean())).sum() - eus_actual)**2
    
    res = minimize_scalar(obj, bounds=[0, 10], method='bounded')
    print(typ, res.x, res.success)
    lot[typ] = lot[typ].apply(scale, args=(res.x, lot[typ].min(), lot[typ].max(), lot[typ].mean()))

    
# Add month and hour of day and max heat flow rate from condenser heat recovery
lot['MaxHeatRecovery'] = lot.Cooling * (1 + 1 / COP_node)
lot['MaxHeatRecovery'] = lot[['MaxHeatRecovery', 'Heating']].min(axis=1)

lot.tail()

Cooling 7.076756405870348 True
Heating 2.59627887025886 True


Cooling       Heating  month  hour  Cooling_raw  \
Date                                                                           
2018-12-31 18:59:59.998  2986.852416  10153.594033     12    18  5233.865122   
2018-12-31 19:59:59.998  2658.570199  10153.845090     12    19  4871.184406   
2018-12-31 20:59:59.998  1876.128175  10129.762689     12    20  4006.755515   
2018-12-31 21:59:59.998  1485.007959  10169.729639     12    21  3574.652425   
2018-12-31 22:59:59.998  1612.909481  10016.574159     12    22  3715.955893   

                          Heating_raw  MaxHeatRecovery  
Date                                                    
2018-12-31 18:59:59.998  32172.215122      3613.980381  
2018-12-31 19:59:59.998  32179.363227      3216.771103  
2018-12-31 20:59:59.998  31493.688348      2270.045343  
2018-12-31 21:59:59.998  32631.628616      1796.804422  
2018-12-31 22:59:59.998  28270.980942      1951.560509

In [247]:
# Check
peak_cooling / lot.loc[lot.Cooling==lot.Cooling.max(), 'Cooling'].values[0], eus_cooling / lot.Cooling.resample("60min").mean().sum() 

(1.0, 1.000003480054735)

In [248]:
# Check
peak_heating / lot.loc[lot.Heating==lot.Heating.max(), 'Heating'].values[0], eus_heating / lot.Heating.resample("60min").mean().sum() 

(1.0, 1.0000046639165672)

In [244]:
toplot = lot[['Cooling', 'Heating', 'Cooling_raw', 'Heating_raw']].melt(ignore_index=False)
# toplot = lot[['Cooling', 'Heating', 'MaxHeatRecovery']].melt(ignore_index=False)
fig = px.line(toplot, x=toplot.index, y='value', color='variable')
fig.update_layout(
    xaxis=dict(
        rangeslider=dict(
            visible=True
        ),
    ),
    yaxis=dict(rangemode='tozero', title='(kW)')
)
fig

In [85]:
toplot = lot[['Cooling', 'Heating', 'MaxHeatRecovery']].resample("60min").mean()
toplot['month'] = toplot.index.month
toplot = toplot.groupby('month').sum()

fig = go.Figure()
fig.add_trace(go.Scatter(x=toplot.index, y=toplot.Cooling, fill='tozeroy', name='Cooling', mode='none'))
fig.add_trace(go.Scatter(x=toplot.index, y=toplot.Heating, fill='tozeroy', name='Heating', mode='none'))
fig.add_trace(go.Scatter(x=toplot.index, y=toplot.MaxHeatRecovery, fill='tozeroy', name='MaxHeatRecovery', mode='none'))

fig.update_layout(title=f'{node} Node - Thermal energy and potential for direct (w/o TES) heat recovery')
fig.update_yaxes(title='(kWh/month)', tickformat="e")
fig.update_xaxes(title='Month', dtick=1)
fig

In [18]:
fig.write_image("fig.svg")

In [86]:
figs = []
for m in pd.unique(lot.month):
    toplot = lot.loc[lot.month==m]
    toplot = toplot.groupby('hour').mean()
    toplot = toplot[['Cooling', 'Heating', 'MaxHeatRecovery']].melt(ignore_index=False)
    fig = px.line(toplot, x=toplot.index + 1, y='value', color='variable', title=dt.date(2000, m, 1).strftime('%B'))
    fig.update_xaxes(title='Hour of the day', dtick=1)
    fig.update_yaxes(title='(kW)', rangemode='tozero')
    figs.append(fig)

In [87]:
figs[4]

In [88]:
figs[8]

In [89]:
figs[11]

# GCHP Design 

> Equations (2) and (3) consider three different pulses of heat to
account for long-term heat imbalances q a , average monthly heat
rates during the design month, and maximum heat rates for a short-
term period during a design day. This period could be as short as 1 h,
but a 4 to 6 h block is recommended.

In [196]:
# Design months
PLFm = lot.resample('1M').mean() 
Ql_4 = lot.resample('240min').mean()
PLFm.Heating = PLFm.Heating / Ql_4.Heating.max()
PLFm.Cooling = PLFm.Cooling / Ql_4.Cooling.max()
max_PLFm = dict(
    Cooling=PLFm.loc[PLFm.Cooling==PLFm.Cooling.max(), 'Cooling'].values[0],
    Heating=PLFm.loc[PLFm.Heating==PLFm.Heating.max(), 'Heating'].values[0],
)
max_PLFm, PLFm

({'Cooling': 0.6753236891728618, 'Heating': 0.872960272869656},
              Cooling   Heating  month       hour  MaxHeatRecovery  \
 Date                                                                
 2018-01-31  0.128662  0.872960    1.0  11.500000      2296.166640   
 2018-02-28  0.219244  0.828462    2.0  11.500000      3085.559911   
 2018-03-31  0.324521  0.787458    3.0  11.500000      3937.513303   
 2018-04-30  0.382544  0.748217    4.0  11.497920      4370.218337   
 2018-05-31  0.513509  0.726533    5.0  11.500000      5296.841103   
 2018-06-30  0.495845  0.703091    6.0  11.500000      5092.981823   
 2018-07-31  0.589576  0.650138    7.0  11.500000      6021.697943   
 2018-08-31  0.629787  0.632562    8.0  11.500000      6198.810900   
 2018-09-30  0.675324  0.622706    9.0  11.500000      6181.777824   
 2018-10-31  0.512934  0.697588   10.0  11.500000      5445.364208   
 2018-11-30  0.327388  0.769953   11.0  11.500000      4352.029220   
 2018-12-31  0.182065  0.8

In [190]:
tmp = loa.loc[loa.BuildingName.str.contains('Tolman'), ['PeakHeating', 'TotalChillerCapacity']]
peak_tolman_heating = tmp.PeakHeating.values[0] * cst.at['kW/(kBtu/h)', 'Value']
peak_tolman_cooling = tmp.TotalChillerCapacity.values[0] * cst.at['kW/ton', 'Value']
peak_tolman_heating, peak_tolman_cooling

(840.693061201908, 2571.6965625)

In [92]:
peak_heating, peak_cooling

(11340.473789644011, 15540.209935557998)

In [93]:
peak_tolman_cooling / peak_cooling

0.16548660366650694

In [94]:
eus.loc[loa.BuildingName.str.contains('Tolman'), ['SpaceHeating', 'DHW', 'Cooling']].applymap("{:.1e}".format)

SpaceHeating      DHW  Cooling
100      3.4e+06  1.5e+06  2.1e+07

In [95]:
eus.set_index('Node').loc[node, ['SpaceHeating', 'DHW', 'Cooling']].sum().map("{:.1e}".format)  # kWh/y

SpaceHeating    5.0e+07
DHW             2.1e+07
Cooling         5.6e+07
dtype: object

In [96]:
# Building area: total gross floor area?
# ETHZ campus Hönggerberg = 360e3 m2 Energy reference area
# EU area = Sum of all above and below ground floor areas for the use of which heating or air conditioning is necessary
# with a total gross floor area of approximately 47,000 m2 (SIA 416) by 2018; experts estimate the associated energy reference area (EBF) to be around 15% smaller
eus.loc[eus.Node==node, 'BuildingArea(sqft)'].sum() * cst.at['m2/sqft', 'Value']

228533.390342

$$ 
Lc = \frac{q_a R_{ga} + (q_{lc}-W_c)(R_b + PLF_m R_{gm} + R_{gd} F{sc})}
{t_g - \frac{t_{wi} + t_{wo}}{2} - t_p}
$$
$$ 
Lh = \frac{q_a R_{ga} + (q_{lh}-W_h)(R_b + PLF_m R_{gm} + R_{gd} F{sc})}
{t_g - \frac{t_{wi} + t_{wo}}{2} - t_p}
$$

*Zhang 2016*
> The total annual heat input to the ground during the cooling mode is entered
as a negative value and must include the heat of compression. The total heat removed during
the heating mode is a positive value

*ASHRAE 2011*
> qa: net annual average heat transfer to ground, kW

In [223]:
# QCond_cool = QEvap + P = QEvap * (1 + 1 / COP_cool)
# QEvap_heat = QCond - P = QCond * (1 - 1 / COP_heat)
COP_HP = 4.1  # To update as the plant should produce HW > 60C for DHW production.
lot['CondRej'] = lot['Cooling'] * (1 + 1 / COP_node)
lot['EvapAbs'] = lot['Heating'] * (1 - 1 / COP_HP)
qa = -lot['CondRej'].mean() + lot['EvapAbs'] .mean()
print(qa, lot['Cooling'].mean(), lot['Heating'].mean(), 'kW')
# Wc: system power input at design cooling load
# Wh: system power input at design heating load
Wc = lot['Cooling'].max() / COP_node
Wh = lot['Heating'].max() / COP_HP
# Equivalent hours at full load
EFLHc = lot['Cooling'].sum() / lot['Cooling'].max()
EFLHh = lot['Heating'].sum() / lot['Heating'].max()
EFLHc, EFLHh

-1612.2461200765374 6367.396995238238 8057.250595230361 kW


(3589.2949908391406, 6223.859472138825)

In [224]:
# Ground temperature t_g = 65 F
tg = (65 - 32) * 5/9  # C  source for tg value: tg = 13.6 from mean annual DBT
# Ground conductivity k_g = 1.4 Btu/(hr*ft*F)
kg = 1.4 * 1.73 # W/(m.K)
# Ground thermal diffusivity a_g = 1 ft^2/day
ag = 1 * 0.3048**2  # m2/d
# Bore fill conductivity k_b = 1 Btu/(hr*ft*F)
k_b = 1 * 1.73 # W/(m.K)
# Static water table at 50 ft below surface = 15.24 m
tg, kg, k_b

(18.333333333333332, 2.4219999999999997, 1.73)

In [225]:
# 25 mm DR11 HDPE pipe, 150 mm borehole, Rb from ASHRAE 2011 Table 6
db = 150e-3
Rb = 0.17

In [226]:
# G factor
t1 = 3650; t2 = 3680; tf = 3680.25  # d
Fof = 4 * ag * tf / db**2
Fo1 = 4 * ag * (tf - t1) / db**2
Fo2 = 4 * ag * (tf - t2) / db**2
Fof, Fo1, Fo2

(60783.362304, 499.61190400000004, 4.129024)

In [227]:
Gf = 0.94; G1 = 0.55; G2 = 0.24
Rga = (Gf - G1) / kg; Rgm = (G1 - G2) / kg; Rgd = G2 / kg
Rga, Rgm, Rgd

(0.16102394715111476, 0.1279933938893477, 0.0990916597853014)

> Selecting twi to be 11
to 17 K higher than t g in cooling and 6 to 11 K lower than tg in heating
is a good compromise between first cost and efficiency in many
regions of the United States.

In [228]:
twi_cool = 30
twi_heat = 10
dt = 5

In [229]:
Fsc = 1.04
tp = -1
Cf = 1.14  # For 20x20 grid
tp = Cf * tp

In [230]:
qlc = Ql_4.Cooling.max()
PLF_m = max_PLFm['Cooling']
twi = twi_cool
two = twi - dt
Lc = (qa * 1e3 * Rga + (qlc - Wc) * 1e3 * (Rb + PLF_m * Rgm + Rgd * Fsc)) / (tg - (twi + two) / 2 - tp)
Lc / 200  # Number of boreholes of 200 m depth

-2534.0370895484944

In [231]:
qlh = Ql_4.Heating.max()
PLF_m = max_PLFm['Heating']
twi = twi_heat
two = twi + dt
Lh = (qa * 1e3 * Rga + (qlh - Wh) * 1e3 * (Rb + PLF_m * Rgm + Rgd * Fsc)) / (tg - (twi + two) / 2 - tp)
Lh / 200  # Number of boreholes of 200 m depth

2056.484720847726

In [232]:
# CHECK
# ETHZ targets 800 boreholes of 200 m to cover 23 GWh heat/year and 22 GWh cold/year
800 * eus_heating / 23e6, 800 * eus_cooling / 22e6

(2454.741237983739, 2027.8846585054189)